In [1]:
import pandas as pd
import numpy as np
import yaml
import os
import logging
import itertools

from datetime import datetime, timedelta
from dateutil import rrule, parser

import os
import warnings
warnings.filterwarnings('ignore')

In [2]:
from deals_utils_v2_2_2 import *
from setup import *
config_file = 'C:/Users/m.sagar/OneDrive - TFO Cloud/Next_Deal_Offer/deal_config.yml'
config = Config(config_file).config

Absent folders were successfully created!


In [3]:
topup = config['deal_recommendation']['topup']
top_n_deals_value = config['deal_recommendation']['top_n_deals_value']

top_aum_criteria_perc = config['deal_recommendation']['top_aum_criteria_perc']
min_value_topup = config['deal_recommendation']['min_value_topup']
buffer_liquidity = config['deal_recommendation']['buffer_liquidity']

# Merging Pos Exposure with Asset Master File

In [4]:
df_nov_exp = pd.read_excel(config['paths']['raw_data']['position_expo_dataset'])
df_asset_master = pd.read_excel(config['paths']['raw_data']['asset_master_dataset'])
df_asset_master_sub = df_asset_master[['ISIN',  'TITLETYPE', 'SPECIFICCLASS', 'MASTERISIN']]

df_nov_exp_2 = pd.merge(df_nov_exp, df_asset_master_sub, on = 'ISIN', how = 'left')
df_nov_exp_2.head(2)

STATUS PORTFOLIONR                 ISIN               DESCRIPTION1  \
0  POSITION      37001P   37001.KK-USD.000.0        Current Account USD   
1  POSITION      37001P  TFOBONASeries000001  BondVest Class A Series 1   

  CODECURRENCY ASSETCLASS       SPV STRATEGY SUBSTRATEGY           AMNT  \
0          USD        AR1       999       CT          CT -295504.006241   
1          USD        AR2  BONDVEST       AR          AR       0.002502   

       QUOTE  MARKET_VALUE_REF  ACCR_INT_REF  BOOK_VALUE_REF  \
0     1.0000    -295504.006241             0  -295504.006241   
1  1451.5078          3.631534             0    -2120.019004   

                                 TITLETYPE SPECIFICCLASS MASTERISIN  
0  Liquidity incl. call deposit (variable)        Others     Others  
1                             Liquid Funds        Others   Bondvest

# Merging the buy date

In [5]:
df_masterisin_isin = df_asset_master[['ISIN','MASTERISIN']]
df_masterisin_isin.drop_duplicates(inplace = True)

df_buy_date = pd.read_excel(config['paths']['raw_data']['buy_date_dataset'])
df_buy_date['PORTFOLIO'] = df_buy_date['PORTFOLIO'].astype(str)
df_buy_date.head(2)

PORTFOLIO            ISIN INITIALBOOKDATE  Year  Month  Day       Date
0     37148   .TFOAGP.X37.A      2017-12-01  2017     12    1 2017-12-01
1     37113  T.FOEQC3.X37.I      2020-06-21  2020      6   21 2020-06-21

In [6]:
df_buy_date = pd.merge(df_buy_date, df_masterisin_isin, on = ['ISIN'], how = 'left')
df_buy_date_sub = df_buy_date[['PORTFOLIO', 'ISIN', 'Date', 'MASTERISIN' ]]
df_buy_date_sub['PORTFOLIO'] = df_buy_date_sub['PORTFOLIO'] + 'P'
df_nov_exp_2['PORTFOLIONR'] = df_nov_exp_2['PORTFOLIONR'].astype(str)
df_buy_date_sub.sort_values(by = ['PORTFOLIO', 'MASTERISIN', 'Date'], inplace= True)
df_buy_date_sub_master = df_buy_date_sub.drop_duplicates(subset= ['PORTFOLIO', 'MASTERISIN'], keep= 'first', inplace= False)
df_buy_date_sub_master = df_buy_date_sub_master[['PORTFOLIO','Date', 'MASTERISIN']] 

df_nov_exp_3 = pd.merge(df_nov_exp_2, df_buy_date_sub_master, left_on = ['PORTFOLIONR', 'MASTERISIN'], right_on= ['PORTFOLIO', 'MASTERISIN'], how = 'left')
df_nov_exp_3.head(2)

STATUS PORTFOLIONR                 ISIN               DESCRIPTION1  \
0  POSITION      37001P   37001.KK-USD.000.0        Current Account USD   
1  POSITION      37001P  TFOBONASeries000001  BondVest Class A Series 1   

  CODECURRENCY ASSETCLASS       SPV STRATEGY SUBSTRATEGY           AMNT  \
0          USD        AR1       999       CT          CT -295504.006241   
1          USD        AR2  BONDVEST       AR          AR       0.002502   

       QUOTE  MARKET_VALUE_REF  ACCR_INT_REF  BOOK_VALUE_REF  \
0     1.0000    -295504.006241             0  -295504.006241   
1  1451.5078          3.631534             0    -2120.019004   

                                 TITLETYPE SPECIFICCLASS MASTERISIN PORTFOLIO  \
0  Liquidity incl. call deposit (variable)        Others     Others    37001P   
1                             Liquid Funds        Others   Bondvest    37001P   

        Date  
0 2005-01-03  
1 2008-06-27

# Filter for Title Type and Specific Class

In [7]:
df_nov_exp_3 = df_nov_exp_3[df_nov_exp_3['SPECIFICCLASS'] == 'Others'] 
df_nov_exp_4 = df_nov_exp_3[df_nov_exp_3['TITLETYPE'] == 'Illiquid Funds'] 
df_nov_exp_5 = df_nov_exp_4[df_nov_exp_4['SUBSTRATEGY'].isin(['CG', 'CY'])]
df_nov_exp_6 = filter_last_2years(df_nov_exp_5)
len(df_nov_exp_3), len(df_nov_exp_4), len(df_nov_exp_5), len(df_nov_exp_6)

(9862, 7986, 7787, 1885)

# Getting the Max SubStrategy & Median


In [8]:
df_nov_exp_6_upd_subset_justmax_strategy = max_substrategy(df_nov_exp_6)

In [9]:
df_nov_exp_6_upd_subset_justmax_strategy_p1 = pd.pivot_table(df_nov_exp_6_upd_subset_justmax_strategy[df_nov_exp_6_upd_subset_justmax_strategy['Is_MaxSubstrategy'] == True], index= ['PORTFOLIONR'], values = ['BOOK_VALUE_REF', 'MASTERISIN'], aggfunc= {'BOOK_VALUE_REF': np.sum, 'MASTERISIN': lambda x: len(x.unique())})
df_nov_exp_6_upd_subset_justmax_strategy_p1.reset_index(inplace= True, drop = False)
df_nov_exp_6_upd_subset_justmax_strategy_p1.columns = ['PORTFOLIONR', 'Total_BOOK_VALUE_REF', 'Unique_MASTERISIN']
df_nov_exp_6_upd_subset_justmax_strategy_p1['Avg_Max_BOOK_VALUE_REF'] = df_nov_exp_6_upd_subset_justmax_strategy_p1['Total_BOOK_VALUE_REF']/df_nov_exp_6_upd_subset_justmax_strategy_p1['Unique_MASTERISIN']
print(df_nov_exp_6_upd_subset_justmax_strategy_p1.head(2))

#Median at MasterISIN level
df_median = df_nov_exp_6_upd_subset_justmax_strategy[df_nov_exp_6_upd_subset_justmax_strategy['Is_MaxSubstrategy'] == True]
df_median_pivot = pd.pivot_table(df_median, index= ['PORTFOLIONR', 'MASTERISIN'], values = ['BOOK_VALUE_REF'], aggfunc=  np.sum )
df_median_pivot.columns = ['BOOK_VALUE_REF']
df_median_pivot.reset_index(inplace= True, drop = False)

df_nov_exp_6_upd_subset_justmax_strategy_p2 = pd.pivot_table(df_median_pivot, index= ['PORTFOLIONR'], values = ['BOOK_VALUE_REF'], aggfunc='median')
df_nov_exp_6_upd_subset_justmax_strategy_p2.reset_index(inplace= True, drop = False)
df_nov_exp_6_upd_subset_justmax_strategy_p2.columns = ['PORTFOLIONR', 'Median_BOOK_VALUE_REF']
print(df_nov_exp_6_upd_subset_justmax_strategy_p2.head(2))

df_nov_exp_6_upd_subset_justmax_strategy_avgBook = pd.merge(df_nov_exp_6_upd_subset_justmax_strategy, df_nov_exp_6_upd_subset_justmax_strategy_p1, 
                                                            on = ['PORTFOLIONR'], how = 'left') 
df_nov_exp_6_upd_subset_justmax_strategy_avgBook = pd.merge(df_nov_exp_6_upd_subset_justmax_strategy_avgBook, df_nov_exp_6_upd_subset_justmax_strategy_p2, 
                                                            on = ['PORTFOLIONR'], how = 'left') 
df_nov_exp_6_upd_subset_justmax_strategy_avgBook.sort_values(by = ['PORTFOLIONR', 'Recent_Phase', 'BOOK_VALUE_REF'],
                                                            ascending= [True, False, False], inplace= True)

df_nov_exp_6_upd_subset_justmax_strategy_avgBook.reset_index(inplace= True, drop = True)
df_nov_exp_6_upd_subset_justmax_strategy_avgBook.head(2)

  PORTFOLIONR  Total_BOOK_VALUE_REF  Unique_MASTERISIN  Avg_Max_BOOK_VALUE_REF
0      37001P           14106422.19                 10             1410642.219
1      37007P             129892.97                  2               64946.485
  PORTFOLIONR  Median_BOOK_VALUE_REF
0      37001P            1662846.720
1      37007P              64946.485


PORTFOLIONR             ISIN       MASTERISIN SUBSTRATEGY  MARKET_VALUE_REF  \
0      37001P  .TFOCLIP2.X37.0          CLIP II          CY        1936053.80   
1      37001P    .TFOCYP.X37.E  Project Liberty          CY        1726523.82   

   BOOK_VALUE_REF   Date_Diff  Less_Than_2_Yrs Max_SubStrategy  \
0       2000000.0  713.396621             True              CY   
1       1800000.0  511.396621             True              CY   

   Is_MaxSubstrategy  Recent_Phase  Total_BOOK_VALUE_REF  Unique_MASTERISIN  \
0               True         False           14106422.19                 10   
1               True         False           14106422.19                 10   

   Avg_Max_BOOK_VALUE_REF  Median_BOOK_VALUE_REF  
0             1410642.219             1662846.72  
1             1410642.219             1662846.72

# Client IPS & DryPowder/ Unplaced Deals Data

## IPS Clients

In [10]:
df_client_ips = pd.read_excel(config['paths']['raw_data']['ips_clients_dataset'])
df_client_ips.fillna(0, inplace= True)
df_client_ips['Mandate'] = df_client_ips['Mandate'].astype(str)
df_client_ips['Mandate'] = df_client_ips['Mandate'] + 'P'
df_client_ips = df_client_ips[df_client_ips['Total'] == 1]
df_client_ips.reset_index(inplace = True, drop = True)
df_client_ips.head(2)

Mandate  AR%   CG%   CY%  Opp%  Total
0  37001P  0.0  0.85  0.15   0.0    1.0
1  37002P  0.4  0.50  0.10   0.0    1.0

## Available Deals

In [11]:
deals = pd.read_excel(config['paths']['raw_data']['available_deals_dataset'])
deals['Date_Today'] = datetime.today()
# datetime.today().strftime("%Y-%m-%d")
deals['Date_Diff'] = deals['Date_Today']- deals['Launch Date']
deals['Date_Diff'] = deals['Date_Diff']/ np.timedelta64(1,'D')
deals['Less_Than_6_Months'] = np.where(deals['Date_Diff']<6*30, True, False)
deals.sort_values(by = ['Less_Than_6_Months', 'Expected MOIC'], ascending= [False, False], inplace= True)
deals.reset_index(inplace = True, drop=True)
deals.head(2)

Deal Launch Date  Dry Powder/ Available amount  \
0  Project Sunrise / Mediawan  2021-09-14                       3375293   
1              Project Magnum  2021-10-28                       5944194   

   Expected IRR  Expected MOIC  Current Valuation (Q3 2021) Capital Yielding  \
0          0.17            2.0                          1.0                0   
1          0.28            1.6                          1.0                0   

  Capital Growth                 Date_Today   Date_Diff  Less_Than_6_Months  
0              G 2022-03-09 09:31:15.587600  176.396708                True  
1              G 2022-03-09 09:31:15.587600  132.396708                True

# Liquidity Data

In [14]:
liquidity = pd.read_excel(config['paths']['raw_data']['liquidity_monitor_dataset'])
liquidity['Cilent Id'] = liquidity['Cilent Id'].astype(str)
liquidity['Cilent Id'] = liquidity['Cilent Id'] + 'P'

value_cols = ['Q1Y1', 'Q2Y1', 'Q3Y1', 'Q4Y1', 'Q1Y2', 'Q2Y2', 'Q3Y2', 'Q4Y2']

liquidity['Min_Liquidity'] = liquidity.apply(lambda x:return_min(x, value_cols, buffer_liquidity ), axis = 1)
liquidity.head(2)

Cilent Id           AUM         Q1Y1          Q2Y1          Q3Y1  \
0    37001P  1.239629e+08  3042882.557  3.189200e+06  2.782312e+06   
1    37002P  7.971613e+06   734324.396  7.343244e+05  9.838812e+05   

           Q4Y1          Q1Y2          Q2Y2          Q3Y2          Q4Y2  \
0  4.194164e+06  8.186136e+06  1.053584e+07  1.812847e+07  2.066214e+07   
1  9.838812e+05  1.441374e+06  1.441374e+06  2.858089e+06  3.111625e+06   

   alert alertInfo  Unnamed: 12  Unnamed: 13  Unnamed: 14  Min_Liquidity  
0   True         H          NaN          NaN          NaN  922868.789503  
1  False   noAlert          NaN          NaN          NaN  614750.197700

In [15]:
liquidity.columns

Index(['Cilent Id', 'AUM', 'Q1Y1', 'Q2Y1', 'Q3Y1', 'Q4Y1', 'Q1Y2', 'Q2Y2',
       'Q3Y2', 'Q4Y2', 'alert', 'alertInfo', 'Unnamed: 12', 'Unnamed: 13',
       'Unnamed: 14', 'Min_Liquidity'],
      dtype='object')

In [16]:
liquidity[['Q1Y1', 'Q2Y1', 'Q3Y1', 'Q4Y1', 'Q1Y2', 'Q2Y2', 'Q3Y2', 'Q4Y2']].min(axis=1)

0      2.782312e+06
1      7.343244e+05
2      3.081356e+05
3      6.878852e+05
4     -1.156551e+06
           ...     
467   -1.650000e+05
468   -2.475000e+05
469    0.000000e+00
470   -1.650000e+05
471    0.000000e+00
Length: 472, dtype: float64

# Recommendation for Non IPS Clients

In [17]:
df_pos_exp_non_ips =  df_nov_exp_6_upd_subset_justmax_strategy_avgBook[~df_nov_exp_6_upd_subset_justmax_strategy_avgBook['PORTFOLIONR'].isin(list(df_client_ips['Mandate']))]
print(len(df_pos_exp_non_ips.PORTFOLIONR.unique())), len(df_nov_exp_6_upd_subset_justmax_strategy_avgBook['PORTFOLIONR'].unique())

dict_clients_deals = {}

for clientid in list(df_nov_exp_4.PORTFOLIONR.unique()):
        dict_clients_deals[clientid] = list((df_nov_exp_4[df_nov_exp_4['PORTFOLIONR'] == clientid]['MASTERISIN']).unique())
        
# dict_clients_deals

129


In [18]:
df_pos_exp_non_ips_client = df_pos_exp_non_ips[['PORTFOLIONR', 'Max_SubStrategy', 'Median_BOOK_VALUE_REF']]
df_pos_exp_non_ips_client.drop_duplicates(inplace= True)
df_pos_exp_non_ips_client.reset_index(inplace = True, drop = True)
len(df_pos_exp_non_ips_client)

129

In [19]:
inactive_non_ips = list(set(df_nov_exp_4['PORTFOLIONR'].unique()) - set(df_client_ips['Mandate'].unique()) - set(df_pos_exp_non_ips['PORTFOLIONR']))
substrategy_list = ['CG', 'CY']
len(inactive_non_ips)

93

In [20]:
df_pos_exp_non_ips_client_2 = pd.DataFrame(index=range(len(inactive_non_ips)*len(substrategy_list)),columns= ['PORTFOLIONR', 'Max_SubStrategy', 'Median_BOOK_VALUE_REF'])
index = 0
for i in itertools.product(inactive_non_ips, substrategy_list):
    df_pos_exp_non_ips_client_2['PORTFOLIONR'][index] = i[0]
    df_pos_exp_non_ips_client_2['Median_BOOK_VALUE_REF'][index] = 0
    df_pos_exp_non_ips_client_2['Max_SubStrategy'][index] = i[1]
    index = index + 1
#     print(i)

In [21]:
df_pos_exp_non_ips_client_2.head(2)

PORTFOLIONR Max_SubStrategy Median_BOOK_VALUE_REF
0      37713P              CG                     0
1      37713P              CY                     0

In [22]:
df_pos_exp_non_ips_client_upd = pd.concat([df_pos_exp_non_ips_client, df_pos_exp_non_ips_client_2])

## Deals to be recommended for non IPS clients

In [23]:
df_client_non_ips_reco = df_pos_exp_non_ips_client_upd.copy()
df_client_non_ips_reco = pd.merge(df_client_non_ips_reco, liquidity[['Cilent Id', 'Min_Liquidity', 'alertInfo', 'AUM']], how = 'left', left_on = 'PORTFOLIONR', right_on= 'Cilent Id')
df_client_non_ips_reco.head(2)

PORTFOLIONR Max_SubStrategy Median_BOOK_VALUE_REF Cilent Id  Min_Liquidity  \
0      37023P              CG              500000.0    37023P            0.0   
1      37114P              CG            178299.905    37114P            0.0   

  alertInfo          AUM  
0         L  20002552.76  
1         L  40461376.99

In [24]:
len(df_client_non_ips_reco['PORTFOLIONR'].unique())

222

In [25]:
deals.rename(columns = {'Deal': 'MASTERISIN'}, inplace = True)
deals.head(2)

MASTERISIN Launch Date  Dry Powder/ Available amount  \
0  Project Sunrise / Mediawan  2021-09-14                       3375293   
1              Project Magnum  2021-10-28                       5944194   

   Expected IRR  Expected MOIC  Current Valuation (Q3 2021) Capital Yielding  \
0          0.17            2.0                          1.0                0   
1          0.28            1.6                          1.0                0   

  Capital Growth                 Date_Today   Date_Diff  Less_Than_6_Months  
0              G 2022-03-09 09:31:15.587600  176.396708                True  
1              G 2022-03-09 09:31:15.587600  132.396708                True

In [26]:
df_client_non_ips_reco.tail(2)

PORTFOLIONR Max_SubStrategy Median_BOOK_VALUE_REF Cilent Id  \
315      37838P              CG                     0    37838P   
316      37838P              CY                     0    37838P   

     Min_Liquidity alertInfo         AUM  
315            0.0         L  1557374.86  
316            0.0         L  1557374.86

In [27]:
# identifier = 313
# clientid = df_client_non_ips_reco['PORTFOLIONR'][identifier]
# substrat = df_client_non_ips_reco['Max_SubStrategy'][identifier]

# expo_df_1  = df_nov_exp_4[df_nov_exp_4['PORTFOLIONR'] == clientid]
# max_substrat_df_1 =  df_client_non_ips_reco[df_client_non_ips_reco['PORTFOLIONR'] == clientid]
# max_substrat_df_1 = max_substrat_df_1[max_substrat_df_1['Max_SubStrategy'] == substrat]
    
# df_temp = deal_sizing(clientid= clientid, max_substrategy = substrat, expo_df = expo_df_1, max_substrat_df =max_substrat_df_1, deals_df = deals, client_deals = dict_clients_deals, topup = True, top_n_deals = 10,
#                      top_aum_criteria_perc = top_aum_criteria_perc, min_value_topup= min_value_topup)
# df_temp

In [72]:
final_non_ips_df = pd.DataFrame(columns= ['PORTFOLIONR', 'MASTERISIN', 'Dry Powder/ Available amount',
                                       'MARKET_VALUE_REF', 'Max_SubStrategy', 'Median_BOOK_VALUE_REF',
                                       'Cilent Id', 'Min_Liquidity', 'alertInfo', 'AUM',
                                       'DEAL_DRYPOWDER_MORE_ALLOCATION',
                                       'DEAL_DRYPOWDER_MORE_ALLOCATION_Boolean', 'Delta_allocation',
                                       'TOPUP_Active', 'UPD_MIN_Liquidity', 'UPD_Liquidity',
                                       'FilterLiquidity', 'VALUE', "Recommendation"])
z = 0
for identifier in range(len(df_client_non_ips_reco)):
#     clientid = '37176P'
    clientid = df_client_non_ips_reco['PORTFOLIONR'][identifier]
    substrat = df_client_non_ips_reco['Max_SubStrategy'][identifier]
    print(clientid)
    
    z = z+1
    expo_df_1  = df_nov_exp_4[df_nov_exp_4['PORTFOLIONR'] == clientid]
    max_substrat_df_1 =  df_client_non_ips_reco[df_client_non_ips_reco['PORTFOLIONR'] == clientid]
    max_substrat_df_1 = max_substrat_df_1[max_substrat_df_1['Max_SubStrategy'] == substrat]
    
    df_temp = deal_sizing(clientid = clientid, max_substrategy = substrat, expo_df = expo_df_1, max_substrat_df =max_substrat_df_1, deals_df = deals, client_deals = dict_clients_deals, topup = True, 
                          top_n_deals = top_n_deals_value, top_aum_criteria_perc = top_aum_criteria_perc, min_value_topup= min_value_topup)
#     print(df_temp)
    final_non_ips_df = pd.concat([final_non_ips_df, df_temp])
final_non_ips_df.head(2)

37023P
CG
   PORTFOLIONR                   MASTERISIN  MARKET_VALUE_REF
0       37023P                         BELK      1.068766e+05
1       37023P             Barry's Addon IV      3.620219e+04
2       37023P              Barrys Addon II      1.118731e+05
3       37023P               Best Logistics      1.016761e+05
4       37023P            Burger King Addon      8.217601e+05
5       37023P                      Burnham      3.352455e+05
6       37023P                      CLIP II      1.663741e+05
7       37023P                        Cabot      7.939543e+05
8       37023P                   China Tech      9.837811e+05
9       37023P                       Encino      5.286899e+05
10      37023P          Envision Healthcare      8.260921e+04
11      37023P          First National Corp      6.800000e+05
12      37023P                  GC Services      2.830244e+04
13      37023P                 Gateway Oaks      5.173138e+05
14      37023P               Hitachi (Koki)      3.427154e+0

3.1111 Check
8
Index(['PORTFOLIONR', 'MASTERISIN', 'Dry Powder/ Available amount',
       'MARKET_VALUE_REF', 'Max_SubStrategy', 'Median_BOOK_VALUE_REF',
       'Cilent Id', 'Min_Liquidity', 'alertInfo', 'AUM', 'UPD_MEDIAN',
       'DEAL_DRYPOWDER_MORE_ALLOCATION',
       'DEAL_DRYPOWDER_MORE_ALLOCATION_Boolean', 'Delta_allocation'],
      dtype='object')
3.2222 Check
7
Index(['PORTFOLIONR', 'MASTERISIN', 'Dry Powder/ Available amount',
       'MARKET_VALUE_REF', 'Max_SubStrategy', 'Median_BOOK_VALUE_REF',
       'Cilent Id', 'Min_Liquidity', 'alertInfo', 'AUM', 'UPD_MEDIAN',
       'DEAL_DRYPOWDER_MORE_ALLOCATION',
       'DEAL_DRYPOWDER_MORE_ALLOCATION_Boolean', 'Delta_allocation'],
      dtype='object')
4 Check
7
Index(['PORTFOLIONR', 'MASTERISIN', 'Dry Powder/ Available amount',
       'MARKET_VALUE_REF', 'Max_SubStrategy', 'Median_BOOK_VALUE_REF',
       'Cilent Id', 'Min_Liquidity', 'alertInfo', 'AUM', 'UPD_MEDIAN',
       'DEAL_DRYPOWDER_MORE_ALLOCATION',
       'DEAL_DRYPOWDER_

2 Check
9
  PORTFOLIONR                          MASTERISIN  \
0      37122P          Project Sunrise / Mediawan   
1      37122P                      Project Magnum   
2      37122P                       Axel Springer   
3      37122P                     Project Ravenna   
4      37122P                             Leonine   
5      37122P       Device Technologies Australia   
6      37122P                 Project Futuristics   
7      37122P      Project Sigma/Flora - Class AK   
8      37122P  Pepper Australia - Class AY Add-on   

   Dry Powder/ Available amount  MARKET_VALUE_REF Max_SubStrategy  \
0                       3375293          0.000000              CG   
1                       5944194          0.000000              CG   
2                       1426496      92986.677729              CG   
3                        700263     104136.708262              CG   
4                       4180906          0.000000              CG   
5                       1376482          0.00

4                        158544.6                                    True  
3 Check
4
Index(['PORTFOLIONR', 'MASTERISIN', 'Dry Powder/ Available amount',
       'MARKET_VALUE_REF', 'Max_SubStrategy', 'Median_BOOK_VALUE_REF',
       'Cilent Id', 'Min_Liquidity', 'alertInfo', 'AUM', 'UPD_MEDIAN',
       'DEAL_DRYPOWDER_MORE_ALLOCATION',
       'DEAL_DRYPOWDER_MORE_ALLOCATION_Boolean'],
      dtype='object')
deals upd
  PORTFOLIONR       MASTERISIN  Dry Powder/ Available amount  \
0      37142P    Project Luxor                       7217500   
1      37142P  Project Liberty                        441132   
2      37142P        LakeHaven                       4393164   
3      37142P  Project Burnham                        450000   

   MARKET_VALUE_REF Max_SubStrategy  Median_BOOK_VALUE_REF Cilent Id  \
0               0.0              CY               291455.4    37142P   
1               0.0              CY               291455.4    37142P   
2               0.0              CY         

1 Check
9
2 Check
9
  PORTFOLIONR                          MASTERISIN  \
0      37158P          Project Sunrise / Mediawan   
1      37158P                      Project Magnum   
2      37158P                       Axel Springer   
3      37158P                     Project Ravenna   
4      37158P                             Leonine   
5      37158P       Device Technologies Australia   
6      37158P                 Project Futuristics   
7      37158P      Project Sigma/Flora - Class AK   
8      37158P  Pepper Australia - Class AY Add-on   

   Dry Powder/ Available amount  MARKET_VALUE_REF Max_SubStrategy  \
0                       3375293          0.000000              CG   
1                       5944194          0.000000              CG   
2                       1426496     143175.584181              CG   
3                        700263     147903.897760              CG   
4                       4180906          0.000000              CG   
5                       1376482    

...

9                      449291.754                                    True  
3 Check
10
Index(['PORTFOLIONR', 'MASTERISIN', 'Dry Powder/ Available amount',
       'MARKET_VALUE_REF', 'Max_SubStrategy', 'Median_BOOK_VALUE_REF',
       'Cilent Id', 'Min_Liquidity', 'alertInfo', 'AUM', 'UPD_MEDIAN',
       'DEAL_DRYPOWDER_MORE_ALLOCATION',
       'DEAL_DRYPOWDER_MORE_ALLOCATION_Boolean'],
      dtype='object')
deals upd
  PORTFOLIONR       MASTERISIN  Dry Powder/ Available amount  \
0      37726P    Project Luxor                       7217500   
1      37726P    Project Luxor                       7217500   
2      37726P  Project Liberty                        441132   
3      37726P  Project Liberty                        441132   
4      37726P   Project Orange                        130422   
5      37726P   Project Orange                        130422   
6      37726P        LakeHaven                       4393164   
7      37726P        LakeHaven                       4393164   
8   

8                                    True  
3 Check
9
Index(['PORTFOLIONR', 'MASTERISIN', 'Dry Powder/ Available amount',
       'MARKET_VALUE_REF', 'Max_SubStrategy', 'Median_BOOK_VALUE_REF',
       'Cilent Id', 'Min_Liquidity', 'alertInfo', 'AUM', 'UPD_MEDIAN',
       'DEAL_DRYPOWDER_MORE_ALLOCATION',
       'DEAL_DRYPOWDER_MORE_ALLOCATION_Boolean'],
      dtype='object')
deals upd
  PORTFOLIONR                          MASTERISIN  \
0      82066P          Project Sunrise / Mediawan   
1      82066P                      Project Magnum   
2      82066P                       Axel Springer   
3      82066P                     Project Ravenna   
4      82066P                             Leonine   
5      82066P       Device Technologies Australia   
6      82066P                 Project Futuristics   
7      82066P      Project Sigma/Flora - Class AK   
8      82066P  Pepper Australia - Class AY Add-on   

   Dry Powder/ Available amount  MARKET_VALUE_REF Max_SubStrategy  \
0            

3 Check
9
Index(['PORTFOLIONR', 'MASTERISIN', 'Dry Powder/ Available amount',
       'MARKET_VALUE_REF', 'Max_SubStrategy', 'Median_BOOK_VALUE_REF',
       'Cilent Id', 'Min_Liquidity', 'alertInfo', 'AUM', 'UPD_MEDIAN',
       'DEAL_DRYPOWDER_MORE_ALLOCATION',
       'DEAL_DRYPOWDER_MORE_ALLOCATION_Boolean'],
      dtype='object')
deals upd
  PORTFOLIONR                          MASTERISIN  \
0      37768P          Project Sunrise / Mediawan   
1      37768P                      Project Magnum   
2      37768P                       Axel Springer   
3      37768P                     Project Ravenna   
4      37768P                             Leonine   
5      37768P       Device Technologies Australia   
6      37768P                 Project Futuristics   
7      37768P      Project Sigma/Flora - Class AK   
8      37768P  Pepper Australia - Class AY Add-on   

   Dry Powder/ Available amount  MARKET_VALUE_REF Max_SubStrategy  \
0                       3375293               0.0        

4 Check
8
Index(['PORTFOLIONR', 'MASTERISIN', 'Dry Powder/ Available amount',
       'MARKET_VALUE_REF', 'Max_SubStrategy', 'Median_BOOK_VALUE_REF',
       'Cilent Id', 'Min_Liquidity', 'alertInfo', 'AUM', 'UPD_MEDIAN',
       'DEAL_DRYPOWDER_MORE_ALLOCATION',
       'DEAL_DRYPOWDER_MORE_ALLOCATION_Boolean', 'Delta_allocation',
       'TOPUP_Active', 'UPD_MIN_Liquidity', 'UPD_Liquidity',
       'FilterLiquidity'],
      dtype='object')
5 Check
1
Index(['PORTFOLIONR', 'MASTERISIN', 'Dry Powder/ Available amount',
       'MARKET_VALUE_REF', 'Max_SubStrategy', 'Median_BOOK_VALUE_REF',
       'Cilent Id', 'Min_Liquidity', 'alertInfo', 'AUM', 'UPD_MEDIAN',
       'DEAL_DRYPOWDER_MORE_ALLOCATION',
       'DEAL_DRYPOWDER_MORE_ALLOCATION_Boolean', 'Delta_allocation',
       'TOPUP_Active', 'UPD_MIN_Liquidity', 'UPD_Liquidity',
       'FilterLiquidity'],
      dtype='object')
37838P
CY
  PORTFOLIONR                  MASTERISIN  MARKET_VALUE_REF
0      37838P                   Crestwood      541

PORTFOLIONR                  MASTERISIN Dry Powder/ Available amount  \
0      37023P  Project Sunrise / Mediawan                      3375293   
0      37114P  Project Sunrise / Mediawan                      3375293   

   MARKET_VALUE_REF Max_SubStrategy  Median_BOOK_VALUE_REF Cilent Id  \
0               0.0              CG             500000.000    37023P   
0               0.0              CG             178299.905    37114P   

   Min_Liquidity alertInfo          AUM  DEAL_DRYPOWDER_MORE_ALLOCATION  \
0            0.0         L  20002552.76                     2875293.000   
0            0.0         L  40461376.99                     3196993.095   

  DEAL_DRYPOWDER_MORE_ALLOCATION_Boolean  Delta_allocation TOPUP_Active  \
0                                   True        500000.000         True   
0                                   True        178299.905         True   

   UPD_MIN_Liquidity UPD_Liquidity FilterLiquidity VALUE Recommendation  \
0                0.0       -500000            True     1              1   
0                0.0       -178299            True     1              1   

   UPD_MEDIAN  
0  500000.000  
0  178299.905

In [73]:
final_non_ips_df.columns

Index(['PORTFOLIONR', 'MASTERISIN', 'Dry Powder/ Available amount',
       'MARKET_VALUE_REF', 'Max_SubStrategy', 'Median_BOOK_VALUE_REF',
       'Cilent Id', 'Min_Liquidity', 'alertInfo', 'AUM',
       'DEAL_DRYPOWDER_MORE_ALLOCATION',
       'DEAL_DRYPOWDER_MORE_ALLOCATION_Boolean', 'Delta_allocation',
       'TOPUP_Active', 'UPD_MIN_Liquidity', 'UPD_Liquidity', 'FilterLiquidity',
       'VALUE', 'Recommendation', 'UPD_MEDIAN'],
      dtype='object')

In [74]:
final_non_ips_df = final_non_ips_df[['PORTFOLIONR', 'Recommendation','MASTERISIN', 'Min_Liquidity', 'alertInfo',  'AUM',
                                    'MARKET_VALUE_REF', 'Max_SubStrategy', 'UPD_MEDIAN','Delta_allocation', 'UPD_Liquidity']]

final_non_ips_df.columns = ['PORTFOLIONR', 'Recommendation_Priority','MASTERISIN', 'Total Allocation Amount', 'Liquidity_alertInfo',  
                            'AUM', 'MARKET_VALUE_REF', 'SUBSTRATEGY', 'Deal_Sizing_MEDIAN','Recommended_allocation', 'UPD_Liquidity']
final_non_ips_df['Is_IPS'] = 'N'
final_non_ips_df.head(2)

PORTFOLIONR Recommendation_Priority                  MASTERISIN  \
0      37023P                       1  Project Sunrise / Mediawan   
0      37114P                       1  Project Sunrise / Mediawan   

   Total Allocation Amount Liquidity_alertInfo          AUM  MARKET_VALUE_REF  \
0                      0.0                   L  20002552.76               0.0   
0                      0.0                   L  40461376.99               0.0   

  SUBSTRATEGY  Deal_Sizing_MEDIAN  Recommended_allocation UPD_Liquidity Is_IPS  
0          CG          500000.000              500000.000       -500000      N  
0          CG          178299.905              178299.905       -178299      N

In [75]:
# final_non_ips_df.to_excel(config['paths']['folders']['result'] + 'final_non_ips_df_3_9.xlsx', index = False)

# Recommendation for IPS Clients

In [32]:
df_nov_exp_4_allocation = current_allocation_underweight(df_nov_exp_4, df_client_ips)
df_nov_exp_4_allocation_ips = df_nov_exp_4_allocation[df_nov_exp_4_allocation['PORTFOLIONR'].isin(list(df_client_ips['Mandate']))]
df_nov_exp_4_allocation_ips.reset_index(inplace= True, drop = True)
df_nov_exp_4_allocation_ips.head(2)

PORTFOLIONR  MARKET_VALUE_REF_AR  MARKET_VALUE_REF_CG  MARKET_VALUE_REF_CY  \
0      37001P                  0.0         9.449350e+07         3.042387e+07   
1      37002P                  0.0         6.017098e+06         0.000000e+00   

   MARKET_VALUE_REF_OP  Total_allocation  Current_AR%  Current_CG%  \
0            1158066.0      1.260754e+08          0.0       0.7495   
1                  0.0      6.017098e+06          0.0       1.0000   

   Current_CY%  Current_OP%  ... Opp%  Total  Delta_AR  Delta_CG  Delta_CY  \
0     0.241315     0.009186  ...  0.0    1.0       0.0    0.1005 -0.091315   
1     0.000000     0.000000  ...  0.0    1.0       0.4   -0.5000  0.100000   

   Delta_OP  Suggest_AR  Suggest_CG  Suggest_CY  Suggest_OP  
0 -0.009186       False        True       False       False  
1  0.000000        True       False        True       False  

[2 rows x 24 columns]

In [33]:
df_pos_exp_ips_client = df_nov_exp_4_allocation_ips[['PORTFOLIONR', 'Suggest_CG', 'Suggest_CY']]

# df_median = df_nov_exp_6_upd_subset_justmax_strategy[df_nov_exp_6_upd_subset_justmax_strategy['Is_MaxSubstrategy'] == True]
df_median_pivot_ips = pd.pivot_table(df_nov_exp_6, index= ['PORTFOLIONR', 'MASTERISIN', 'SUBSTRATEGY'], values = ['BOOK_VALUE_REF'], aggfunc=  np.sum )
df_median_pivot_ips.columns = ['BOOK_VALUE_REF']
df_median_pivot_ips.reset_index(inplace= True, drop = False)

df_nov_exp_6_strat_median = pd.pivot_table(df_median_pivot_ips, index =['PORTFOLIONR'], columns= ['SUBSTRATEGY'], values = ['BOOK_VALUE_REF'], aggfunc= np.median)
df_nov_exp_6_strat_median.fillna(0, inplace= True)
list_cols = []
for i in df_nov_exp_6_strat_median.columns:
    z = 'Median_Book_' + i[1]
    list_cols.append(z)

df_nov_exp_6_strat_median.columns = list_cols
df_nov_exp_6_strat_median.reset_index(inplace= True, drop = False)

df_pos_exp_ips_client = pd.merge(df_pos_exp_ips_client, df_nov_exp_6_strat_median, on = ['PORTFOLIONR'], how = 'left')
df_pos_exp_ips_client.fillna(0, inplace= True)
df_pos_exp_ips_client.head(2)

PORTFOLIONR  Suggest_CG  Suggest_CY  Median_Book_CG  Median_Book_CY
0      37001P        True       False      326561.515      1662846.72
1      37002P       False        True           0.000            0.00

In [34]:
df_pos_exp_ips_client = pd.merge(df_pos_exp_ips_client, liquidity[['Cilent Id', 'Min_Liquidity', 'alertInfo', 'AUM']], how = 'left', left_on = 'PORTFOLIONR', right_on= 'Cilent Id')
print(len(df_pos_exp_ips_client))
df_pos_exp_ips_client.drop_duplicates(inplace= True)
print(len(df_pos_exp_ips_client))
df_pos_exp_ips_client.head(2)

80
77


PORTFOLIONR  Suggest_CG  Suggest_CY  Median_Book_CG  Median_Book_CY  \
0      37001P        True       False      326561.515      1662846.72   
1      37002P       False        True           0.000            0.00   

  Cilent Id  Min_Liquidity alertInfo           AUM  
0    37001P  922868.789503         H  1.239629e+08  
1    37002P  614750.197700   noAlert  7.971613e+06

In [35]:
final_ips_df = pd.DataFrame(columns= ['PORTFOLIONR', 'MASTERISIN', 'Dry Powder/ Available amount',
       'MARKET_VALUE_REF', 'Suggest_CG', 'Suggest_CY', 'Median_Book_CG',
       'Median_Book_CY', 'Cilent Id', 'Min_Liquidity', 'alertInfo', 'AUM',
       'DEAL_DRYPOWDER_MORE_ALLOCATION',
       'DEAL_DRYPOWDER_MORE_ALLOCATION_Boolean', 'Delta_allocation',
       'TOPUP_Active', 'UPD_MIN_Liquidity', 'UPD_Liquidity', 'FilterLiquidity',
       'VALUE', 'Recommendation', 'UPD_MEDIAN'])

for clientid in list(df_pos_exp_ips_client.PORTFOLIONR):
#     clientid = '37176P'
    print(clientid)
    expo_df_1  = df_nov_exp_4[df_nov_exp_4['PORTFOLIONR'] == clientid]
    max_substrat_df_1 =  df_pos_exp_ips_client[df_pos_exp_ips_client['PORTFOLIONR'] == clientid]
    df_temp = deal_sizing_ips(clientid = clientid, expo_df_def1 = expo_df_1, suggest_substrat_df_def1 =max_substrat_df_1, 
                              deals_df_def1 = deals, client_deals_def1 = dict_clients_deals, topup = True, 
                              top_n_deals_def1 = 10,  
                              top_aum_criteria_perc = top_aum_criteria_perc,  
                              min_value_topup = min_value_topup)
    final_ips_df = pd.concat([final_ips_df, df_temp])
    final_ips_df.reset_index(inplace= True, drop = True)
final_ips_df.head(2)

37001P
True
9
                           MASTERISIN Launch Date  \
0          Project Sunrise / Mediawan  2021-09-14   
1                      Project Magnum  2021-10-28   
2                       Axel Springer  2019-11-25   
3                     Project Ravenna  2019-02-07   
4                             Leonine  2019-04-18   
5       Device Technologies Australia  2018-11-27   
6                 Project Futuristics  2019-03-20   
7      Project Sigma/Flora - Class AK  2019-04-24   
8  Pepper Australia - Class AY Add-on  2019-07-22   

   Dry Powder/ Available amount  Expected IRR  Expected MOIC  \
0                       3375293         0.170            2.0   
1                       5944194         0.280            1.6   
2                       1426496         0.143            1.9   
3                        700263         0.126            1.8   
4                       4180906         0.121            1.7   
5                       1376482         0.119            1.7   
6      

check 0
  PORTFOLIONR                          MASTERISIN  \
0      37007P          Project Sunrise / Mediawan   
1      37007P                      Project Magnum   
2      37007P                       Axel Springer   
3      37007P                     Project Ravenna   
4      37007P                             Leonine   
5      37007P       Device Technologies Australia   
6      37007P                 Project Futuristics   
7      37007P      Project Sigma/Flora - Class AK   
8      37007P  Pepper Australia - Class AY Add-on   

   Dry Powder/ Available amount  MARKET_VALUE_REF  Suggest_CG  Suggest_CY  \
0                       3375293               0.0        True       False   
1                       5944194               0.0        True       False   
2                       1426496               0.0        True       False   
3                        700263               0.0        True       False   
4                       4180906               0.0        True       False   

37034P
False
        MASTERISIN Launch Date  Dry Powder/ Available amount  Expected IRR  \
0    Project Luxor  2021-11-22                       7217500         0.080   
1  Project Liberty  2020-10-26                        441132         0.100   
2   Project Orange  2020-01-28                        130422         0.095   
3        LakeHaven  2021-04-29                       4393164         0.095   
4  Project Burnham  2019-08-14                        450000         0.090   

   Expected MOIC  Current Valuation (Q3 2021) Capital Yielding Capital Growth  \
0            1.4                         1.00                Y              0   
1            1.5                         0.92                Y              0   
2            1.5                         0.90                Y              0   
3            1.5                         0.95                Y              0   
4            1.4                         0.80                Y              0   

                  Date_Today   

  PORTFOLIONR       MASTERISIN  Dry Powder/ Available amount  \
0      37037P    Project Luxor                       7217500   
1      37037P  Project Liberty                        441132   
2      37037P   Project Orange                        130422   
3      37037P        LakeHaven                       4393164   
4      37037P  Project Burnham                        450000   

   MARKET_VALUE_REF  Suggest_CG  Suggest_CY  Median_Book_CG  Median_Book_CY  \
0          0.000000       False        True       2000000.0       343464.85   
1          0.000000       False        True       2000000.0       343464.85   
2     274047.690528       False        True       2000000.0       343464.85   
3          0.000000       False        True       2000000.0       343464.85   
4          0.000000       False        True       2000000.0       343464.85   

  Cilent Id  Min_Liquidity alertInfo          AUM  
0    37037P  453438.789834   noAlert  29921014.95  
1    37037P  453438.789834   noAlert

8  9255021.22  
deals_available_sub_strategy_upd
  PORTFOLIONR                          MASTERISIN  \
0      37044P          Project Sunrise / Mediawan   
1      37044P                      Project Magnum   
2      37044P                       Axel Springer   
3      37044P                     Project Ravenna   
4      37044P                             Leonine   
5      37044P       Device Technologies Australia   
6      37044P                 Project Futuristics   
7      37044P      Project Sigma/Flora - Class AK   
8      37044P  Pepper Australia - Class AY Add-on   

   Dry Powder/ Available amount  MARKET_VALUE_REF  Suggest_CG  Suggest_CY  \
0                       3375293               0.0        True        True   
1                       5944194               0.0        True        True   
2                       1426496               0.0        True        True   
3                        700263               0.0        True        True   
4                       4180906    

...

True
9
                           MASTERISIN Launch Date  \
0          Project Sunrise / Mediawan  2021-09-14   
1                      Project Magnum  2021-10-28   
2                       Axel Springer  2019-11-25   
3                     Project Ravenna  2019-02-07   
4                             Leonine  2019-04-18   
5       Device Technologies Australia  2018-11-27   
6                 Project Futuristics  2019-03-20   
7      Project Sigma/Flora - Class AK  2019-04-24   
8  Pepper Australia - Class AY Add-on  2019-07-22   

   Dry Powder/ Available amount  Expected IRR  Expected MOIC  \
0                       3375293         0.170            2.0   
1                       5944194         0.280            1.6   
2                       1426496         0.143            1.9   
3                        700263         0.126            1.8   
4                       4180906         0.121            1.7   
5                       1376482         0.119            1.7   
6             

False
        MASTERISIN Launch Date  Dry Powder/ Available amount  Expected IRR  \
0    Project Luxor  2021-11-22                       7217500         0.080   
1  Project Liberty  2020-10-26                        441132         0.100   
2   Project Orange  2020-01-28                        130422         0.095   
3        LakeHaven  2021-04-29                       4393164         0.095   
4  Project Burnham  2019-08-14                        450000         0.090   

   Expected MOIC  Current Valuation (Q3 2021) Capital Yielding Capital Growth  \
0            1.4                         1.00                Y              0   
1            1.5                         0.92                Y              0   
2            1.5                         0.90                Y              0   
3            1.5                         0.95                Y              0   
4            1.4                         0.80                Y              0   

                  Date_Today   Date_Di

4 2022-03-09 09:31:15.587600  938.396708               False  
7217500
check 0.1
  PORTFOLIONR       MASTERISIN  Dry Powder/ Available amount  MARKET_VALUE_REF
0      82002P    Project Luxor                       7217500               NaN
1      82002P  Project Liberty                        441132      143410.87500
2      82002P   Project Orange                        130422       41088.58758
3      82002P        LakeHaven                       4393164               NaN
4      82002P  Project Burnham                        450000               NaN
check 0.2
  PORTFOLIONR       MASTERISIN  Dry Powder/ Available amount  \
0      82002P    Project Luxor                       7217500   
1      82002P  Project Liberty                        441132   
2      82002P   Project Orange                        130422   
3      82002P        LakeHaven                       4393164   
4      82002P  Project Burnham                        450000   

   MARKET_VALUE_REF  Suggest_CG  Suggest_CY  Media

82027P
False
82053P
False
        MASTERISIN Launch Date  Dry Powder/ Available amount  Expected IRR  \
0    Project Luxor  2021-11-22                       7217500         0.080   
1  Project Liberty  2020-10-26                        441132         0.100   
2   Project Orange  2020-01-28                        130422         0.095   
3        LakeHaven  2021-04-29                       4393164         0.095   
4  Project Burnham  2019-08-14                        450000         0.090   

   Expected MOIC  Current Valuation (Q3 2021) Capital Yielding Capital Growth  \
0            1.4                         1.00                Y              0   
1            1.5                         0.92                Y              0   
2            1.5                         0.90                Y              0   
3            1.5                         0.95                Y              0   
4            1.4                         0.80                Y              0   

                  

PORTFOLIONR                  MASTERISIN Dry Powder/ Available amount  \
0      37001P  Project Sunrise / Mediawan                      3375293   
1      37001P              Project Magnum                      5944194   

   MARKET_VALUE_REF Suggest_CG Suggest_CY  Median_Book_CG  Median_Book_CY  \
0               0.0       True      False      326561.515      1662846.72   
1               0.0       True      False      326561.515      1662846.72   

  Cilent Id  Min_Liquidity  ... DEAL_DRYPOWDER_MORE_ALLOCATION_Boolean  \
0    37001P  922868.789503  ...                                   True   
1    37001P  922868.789503  ...                                   True   

   Delta_allocation  TOPUP_Active UPD_MIN_Liquidity  UPD_Liquidity  \
0        326561.515          True     922868.789503         596307   
1        326561.515          True     922868.789503         269745   

  FilterLiquidity  VALUE Recommendation  UPD_MEDIAN SUBSTRATEGY  
0            True      1              1  326561.515          CG  
1            True      1              2  326561.515          CG  

[2 rows x 23 columns]

In [36]:
final_ips_df.tail(10)

PORTFOLIONR                          MASTERISIN  \
160      82006P                             Leonine   
161      82006P       Device Technologies Australia   
162      82006P                 Project Futuristics   
163      82006P      Project Sigma/Flora - Class AK   
164      82006P  Pepper Australia - Class AY Add-on   
165      82007P          Project Sunrise / Mediawan   
166      82007P                      Project Magnum   
167      82007P                       Axel Springer   
168      82053P                       Project Luxor   
169      82079P                       Project Luxor   

    Dry Powder/ Available amount  MARKET_VALUE_REF Suggest_CG Suggest_CY  \
160                      4180906               0.0       True      False   
161                      1376482               0.0       True      False   
162                      3261508               0.0       True      False   
163                       117029               0.0       True      False   
164                       251364               0.0       True      False   
165                      3375293               0.0       True      False   
166                      5944194               0.0       True      False   
167                      1426496               0.0       True      False   
168                      7217500               0.0      False       True   
169                      7217500               0.0      False       True   

     Median_Book_CG  Median_Book_CY Cilent Id  Min_Liquidity  ...  \
160        26105.75        0.000000    82006P   638982.95900  ...   
161        26105.75        0.000000    82006P   638982.95900  ...   
162        26105.75        0.000000    82006P   638982.95900  ...   
163        26105.75        0.000000    82006P   638982.95900  ...   
164        26105.75        0.000000    82006P   638982.95900  ...   
165            0.00        0.000000    82007P   371738.09285  ...   
166            0.00        0.000000    82007P   371738.09285  ...   
167            0.00        0.000000    82007P   371738.09285  ...   
168       170166.00   285876.000055    82053P        0.00000  ...   
169        58645.71   256130.600000    82079P        0.00000  ...   

    DEAL_DRYPOWDER_MORE_ALLOCATION_Boolean  Delta_allocation  TOPUP_Active  \
160                                   True      26105.750000          True   
161                                   True      26105.750000          True   
162                                   True      26105.750000          True   
163                                   True      26105.750000          True   
164                                   True      26105.750000          True   
165                                   True     128440.046130          True   
166                                   True     128440.046130          True   
167                                   True     128440.046130          True   
168                                   True     285876.000055          True   
169                                   True     256130.600000          True   

    UPD_MIN_Liquidity  UPD_Liquidity FilterLiquidity  VALUE Recommendation  \
160      638982.95900         534559            True      1              4   
161      638982.95900         508453            True      1              5   
162      638982.95900         482347            True      1              6   
163      638982.95900         456241            True      1              7   
164      638982.95900         430135            True      1              8   
165      371738.09285         243298            True      1              1   
166      371738.09285         114857            True      1              2   
167      371738.09285         -13583            True      1              3   
168           0.00000        -285876            True      1              1   
169           0.00000        -256130            True      1              1   

        UPD_MEDIAN SUBSTRATEGY  
160   26105.750000          CG  
161   26105.75000

In [37]:
len_additional_ips = len(set(df_pos_exp_ips_client['PORTFOLIONR']) - set(final_ips_df.PORTFOLIONR))
list_additional_ips = list(set(df_pos_exp_ips_client['PORTFOLIONR']) - set(final_ips_df.PORTFOLIONR))

In [38]:
z = 0
df_ips_concat = pd.DataFrame(index = range(len_additional_ips),columns = ['PORTFOLIONR'])
for i in range(len_additional_ips):
#     print(i)
    df_ips_concat['PORTFOLIONR'][i] = list_additional_ips[z]
    z = z+1
df_ips_concat
df_ips_concat['Suggest_CG'] = False
df_ips_concat['Suggest_CY'] = False

In [76]:
final_ips_df_upd = pd.concat([final_ips_df, df_ips_concat])
# final_ips_df_upd.tail(20)

In [77]:
final_ips_df_upd.columns

Index(['PORTFOLIONR', 'MASTERISIN', 'Dry Powder/ Available amount',
       'MARKET_VALUE_REF', 'Suggest_CG', 'Suggest_CY', 'Median_Book_CG',
       'Median_Book_CY', 'Cilent Id', 'Min_Liquidity', 'alertInfo', 'AUM',
       'DEAL_DRYPOWDER_MORE_ALLOCATION',
       'DEAL_DRYPOWDER_MORE_ALLOCATION_Boolean', 'Delta_allocation',
       'TOPUP_Active', 'UPD_MIN_Liquidity', 'UPD_Liquidity', 'FilterLiquidity',
       'VALUE', 'Recommendation', 'UPD_MEDIAN', 'SUBSTRATEGY'],
      dtype='object')

In [78]:
final_ips_df_upd = final_ips_df_upd[['PORTFOLIONR', 'Recommendation','MASTERISIN', 'Min_Liquidity', 'alertInfo',  'AUM',
                                    'MARKET_VALUE_REF', 'SUBSTRATEGY', 'UPD_MEDIAN','Delta_allocation', 'UPD_Liquidity']]
final_ips_df_upd.columns = ['PORTFOLIONR', 'Recommendation_Priority','MASTERISIN', 'Total Allocation Amount', 'Liquidity_alertInfo',  
                            'AUM', 'MARKET_VALUE_REF', 'SUBSTRATEGY', 'Deal_Sizing_MEDIAN','Recommended_allocation', 'UPD_Liquidity']
final_ips_df_upd['Is_IPS'] = 'Y'


In [79]:
final_ips_nonips_df_upd = pd.concat([final_ips_df_upd, final_non_ips_df])
final_ips_nonips_df_upd.head(2)

PORTFOLIONR Recommendation_Priority                  MASTERISIN  \
0      37001P                       1  Project Sunrise / Mediawan   
1      37001P                       2              Project Magnum   

   Total Allocation Amount Liquidity_alertInfo           AUM  \
0            922868.789503                   H  1.239629e+08   
1            922868.789503                   H  1.239629e+08   

   MARKET_VALUE_REF SUBSTRATEGY  Deal_Sizing_MEDIAN  Recommended_allocation  \
0               0.0          CG          326561.515              326561.515   
1               0.0          CG          326561.515              326561.515   

  UPD_Liquidity Is_IPS  
0        596307      Y  
1        269745      Y

In [80]:
buffer_percentage = config['deal_recommendation']['buffer_liquidity'] 

In [81]:
final_ips_nonips_df_upd['Buffer Liquidity Amount'] = final_ips_nonips_df_upd['UPD_Liquidity'] + (buffer_percentage/100)*final_ips_nonips_df_upd['AUM']

In [82]:
final_ips_nonips_df_upd['Buffer Liquidity Percentage'] = final_ips_nonips_df_upd['Buffer Liquidity Amount']/final_ips_nonips_df_upd['AUM']

In [86]:
final_ips_nonips_df_upd.drop(columns=['UPD_Liquidity'], inplace= True)

KeyError: "['UPD_Liquidity'] not found in axis"

In [87]:
final_ips_nonips_df_upd.head(2)

PORTFOLIONR Recommendation_Priority                  MASTERISIN  \
0      37001P                       1  Project Sunrise / Mediawan   
1      37001P                       2              Project Magnum   

   Total Allocation Amount Liquidity_alertInfo           AUM  \
0            922868.789503                   H  1.239629e+08   
1            922868.789503                   H  1.239629e+08   

   MARKET_VALUE_REF SUBSTRATEGY  Deal_Sizing_MEDIAN  Recommended_allocation  \
0               0.0          CG          326561.515              326561.515   
1               0.0          CG          326561.515              326561.515   

  Is_IPS Buffer Liquidity Amount Buffer Liquidity Percentage  
0      Y            2455749.8892                     0.01981  
1      Y            2129187.8892                    0.017176

In [85]:
final_ips_nonips_df_upd[final_ips_nonips_df_upd['PORTFOLIONR'] == '37001P'].to_clipboard()

In [89]:
# final_ips_df_upd.to_excel(config['paths']['folders']['result'] + 'final_ips_df_upd_3_9.xlsx', index = False)
final_ips_nonips_df_upd.to_excel(config['paths']['folders']['result'] + 'final_ips_nonips_df_upd_3_9.xlsx', index = False)